In [10]:
from keras.optimizers import SGD
from keras.layers import Input, Dense, Convolution2D, MaxPooling2D, AveragePooling2D, ZeroPadding2D, Dropout, Flatten, merge, Reshape, Activation
from keras.datasets import cifar10
from keras.regularizers import l2
from keras.models import Model, Sequential
from keras.preprocessing import image

from sklearn.metrics import log_loss

from custom_layers.googlenet_custom_layers import LRN, PoolHelper

import numpy as np

# from load_cifar10 import load_cifar10_data
import vgg16 as jeremy_vgg16

In [2]:
def googlenet_model(img_rows, img_cols, channel=1, num_classes=None):
    """
    GoogLeNet a.k.a. Inception v1 for Keras

    Model Schema is based on
    https://gist.github.com/joelouismarino/a2ede9ab3928f999575423b9887abd14

    ImageNet Pretrained Weights
    https://drive.google.com/open?id=0B319laiAPjU3RE1maU9MMlh2dnc

    Blog Post:
    http://joelouismarino.github.io/blog_posts/blog_googlenet_keras.html

    Parameters:
      img_rows, img_cols - resolution of inputs
      channel - 1 for grayscale, 3 for color
      num_classes - number of class labels for our classification task
    """

    input = Input(shape=(channel, img_rows, img_cols))
    conv1_7x7_s2 = Convolution2D(64,7,7,subsample=(2,2),border_mode='same',activation='relu',name='conv1/7x7_s2',W_regularizer=l2(0.0002))(input)
    conv1_zero_pad = ZeroPadding2D(padding=(1, 1))(conv1_7x7_s2)
    pool1_helper = PoolHelper()(conv1_zero_pad)
    pool1_3x3_s2 = MaxPooling2D(pool_size=(3,3),strides=(2,2),border_mode='valid',name='pool1/3x3_s2')(pool1_helper)
    pool1_norm1 = LRN(name='pool1/norm1')(pool1_3x3_s2)
    conv2_3x3_reduce = Convolution2D(64,1,1,border_mode='same',activation='relu',name='conv2/3x3_reduce',W_regularizer=l2(0.0002))(pool1_norm1)
    conv2_3x3 = Convolution2D(192,3,3,border_mode='same',activation='relu',name='conv2/3x3',W_regularizer=l2(0.0002))(conv2_3x3_reduce)
    conv2_norm2 = LRN(name='conv2/norm2')(conv2_3x3)
    conv2_zero_pad = ZeroPadding2D(padding=(1, 1))(conv2_norm2)
    pool2_helper = PoolHelper()(conv2_zero_pad)
    pool2_3x3_s2 = MaxPooling2D(pool_size=(3,3),strides=(2,2),border_mode='valid',name='pool2/3x3_s2')(pool2_helper)

    inception_3a_1x1 = Convolution2D(64,1,1,border_mode='same',activation='relu',name='inception_3a/1x1',W_regularizer=l2(0.0002))(pool2_3x3_s2)
    inception_3a_3x3_reduce = Convolution2D(96,1,1,border_mode='same',activation='relu',name='inception_3a/3x3_reduce',W_regularizer=l2(0.0002))(pool2_3x3_s2)
    inception_3a_3x3 = Convolution2D(128,3,3,border_mode='same',activation='relu',name='inception_3a/3x3',W_regularizer=l2(0.0002))(inception_3a_3x3_reduce)
    inception_3a_5x5_reduce = Convolution2D(16,1,1,border_mode='same',activation='relu',name='inception_3a/5x5_reduce',W_regularizer=l2(0.0002))(pool2_3x3_s2)
    inception_3a_5x5 = Convolution2D(32,5,5,border_mode='same',activation='relu',name='inception_3a/5x5',W_regularizer=l2(0.0002))(inception_3a_5x5_reduce)
    inception_3a_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_3a/pool')(pool2_3x3_s2)
    inception_3a_pool_proj = Convolution2D(32,1,1,border_mode='same',activation='relu',name='inception_3a/pool_proj',W_regularizer=l2(0.0002))(inception_3a_pool)
    inception_3a_output = merge([inception_3a_1x1,inception_3a_3x3,inception_3a_5x5,inception_3a_pool_proj],mode='concat',concat_axis=1,name='inception_3a/output')

    inception_3b_1x1 = Convolution2D(128,1,1,border_mode='same',activation='relu',name='inception_3b/1x1',W_regularizer=l2(0.0002))(inception_3a_output)
    inception_3b_3x3_reduce = Convolution2D(128,1,1,border_mode='same',activation='relu',name='inception_3b/3x3_reduce',W_regularizer=l2(0.0002))(inception_3a_output)
    inception_3b_3x3 = Convolution2D(192,3,3,border_mode='same',activation='relu',name='inception_3b/3x3',W_regularizer=l2(0.0002))(inception_3b_3x3_reduce)
    inception_3b_5x5_reduce = Convolution2D(32,1,1,border_mode='same',activation='relu',name='inception_3b/5x5_reduce',W_regularizer=l2(0.0002))(inception_3a_output)
    inception_3b_5x5 = Convolution2D(96,5,5,border_mode='same',activation='relu',name='inception_3b/5x5',W_regularizer=l2(0.0002))(inception_3b_5x5_reduce)
    inception_3b_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_3b/pool')(inception_3a_output)
    inception_3b_pool_proj = Convolution2D(64,1,1,border_mode='same',activation='relu',name='inception_3b/pool_proj',W_regularizer=l2(0.0002))(inception_3b_pool)
    inception_3b_output = merge([inception_3b_1x1,inception_3b_3x3,inception_3b_5x5,inception_3b_pool_proj],mode='concat',concat_axis=1,name='inception_3b/output')

    inception_3b_output_zero_pad = ZeroPadding2D(padding=(1, 1))(inception_3b_output)
    pool3_helper = PoolHelper()(inception_3b_output_zero_pad)
    pool3_3x3_s2 = MaxPooling2D(pool_size=(3,3),strides=(2,2),border_mode='valid',name='pool3/3x3_s2')(pool3_helper)

    inception_4a_1x1 = Convolution2D(192,1,1,border_mode='same',activation='relu',name='inception_4a/1x1',W_regularizer=l2(0.0002))(pool3_3x3_s2)
    inception_4a_3x3_reduce = Convolution2D(96,1,1,border_mode='same',activation='relu',name='inception_4a/3x3_reduce',W_regularizer=l2(0.0002))(pool3_3x3_s2)
    inception_4a_3x3 = Convolution2D(208,3,3,border_mode='same',activation='relu',name='inception_4a/3x3',W_regularizer=l2(0.0002))(inception_4a_3x3_reduce)
    inception_4a_5x5_reduce = Convolution2D(16,1,1,border_mode='same',activation='relu',name='inception_4a/5x5_reduce',W_regularizer=l2(0.0002))(pool3_3x3_s2)
    inception_4a_5x5 = Convolution2D(48,5,5,border_mode='same',activation='relu',name='inception_4a/5x5',W_regularizer=l2(0.0002))(inception_4a_5x5_reduce)
    inception_4a_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_4a/pool')(pool3_3x3_s2)
    inception_4a_pool_proj = Convolution2D(64,1,1,border_mode='same',activation='relu',name='inception_4a/pool_proj',W_regularizer=l2(0.0002))(inception_4a_pool)
    inception_4a_output = merge([inception_4a_1x1,inception_4a_3x3,inception_4a_5x5,inception_4a_pool_proj],mode='concat',concat_axis=1,name='inception_4a/output')

    loss1_ave_pool = AveragePooling2D(pool_size=(5,5),strides=(3,3),name='loss1/ave_pool')(inception_4a_output)
    loss1_conv = Convolution2D(128,1,1,border_mode='same',activation='relu',name='loss1/conv',W_regularizer=l2(0.0002))(loss1_ave_pool)
    loss1_flat = Flatten()(loss1_conv)
    loss1_fc = Dense(1024,activation='relu',name='loss1/fc',W_regularizer=l2(0.0002))(loss1_flat)
    loss1_drop_fc = Dropout(0.7)(loss1_fc)
    loss1_classifier = Dense(1000,name='loss1/classifier',W_regularizer=l2(0.0002))(loss1_drop_fc)
    loss1_classifier_act = Activation('softmax')(loss1_classifier)

    inception_4b_1x1 = Convolution2D(160,1,1,border_mode='same',activation='relu',name='inception_4b/1x1',W_regularizer=l2(0.0002))(inception_4a_output)
    inception_4b_3x3_reduce = Convolution2D(112,1,1,border_mode='same',activation='relu',name='inception_4b/3x3_reduce',W_regularizer=l2(0.0002))(inception_4a_output)
    inception_4b_3x3 = Convolution2D(224,3,3,border_mode='same',activation='relu',name='inception_4b/3x3',W_regularizer=l2(0.0002))(inception_4b_3x3_reduce)
    inception_4b_5x5_reduce = Convolution2D(24,1,1,border_mode='same',activation='relu',name='inception_4b/5x5_reduce',W_regularizer=l2(0.0002))(inception_4a_output)
    inception_4b_5x5 = Convolution2D(64,5,5,border_mode='same',activation='relu',name='inception_4b/5x5',W_regularizer=l2(0.0002))(inception_4b_5x5_reduce)
    inception_4b_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_4b/pool')(inception_4a_output)
    inception_4b_pool_proj = Convolution2D(64,1,1,border_mode='same',activation='relu',name='inception_4b/pool_proj',W_regularizer=l2(0.0002))(inception_4b_pool)
    inception_4b_output = merge([inception_4b_1x1,inception_4b_3x3,inception_4b_5x5,inception_4b_pool_proj],mode='concat',concat_axis=1,name='inception_4b_output')
    
    inception_4c_1x1 = Convolution2D(128,1,1,border_mode='same',activation='relu',name='inception_4c/1x1',W_regularizer=l2(0.0002))(inception_4b_output)
    inception_4c_3x3_reduce = Convolution2D(128,1,1,border_mode='same',activation='relu',name='inception_4c/3x3_reduce',W_regularizer=l2(0.0002))(inception_4b_output)
    inception_4c_3x3 = Convolution2D(256,3,3,border_mode='same',activation='relu',name='inception_4c/3x3',W_regularizer=l2(0.0002))(inception_4c_3x3_reduce)
    inception_4c_5x5_reduce = Convolution2D(24,1,1,border_mode='same',activation='relu',name='inception_4c/5x5_reduce',W_regularizer=l2(0.0002))(inception_4b_output)
    inception_4c_5x5 = Convolution2D(64,5,5,border_mode='same',activation='relu',name='inception_4c/5x5',W_regularizer=l2(0.0002))(inception_4c_5x5_reduce)
    inception_4c_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_4c/pool')(inception_4b_output)
    inception_4c_pool_proj = Convolution2D(64,1,1,border_mode='same',activation='relu',name='inception_4c/pool_proj',W_regularizer=l2(0.0002))(inception_4c_pool)
    inception_4c_output = merge([inception_4c_1x1,inception_4c_3x3,inception_4c_5x5,inception_4c_pool_proj],mode='concat',concat_axis=1,name='inception_4c/output')

    inception_4d_1x1 = Convolution2D(112,1,1,border_mode='same',activation='relu',name='inception_4d/1x1',W_regularizer=l2(0.0002))(inception_4c_output)
    inception_4d_3x3_reduce = Convolution2D(144,1,1,border_mode='same',activation='relu',name='inception_4d/3x3_reduce',W_regularizer=l2(0.0002))(inception_4c_output)
    inception_4d_3x3 = Convolution2D(288,3,3,border_mode='same',activation='relu',name='inception_4d/3x3',W_regularizer=l2(0.0002))(inception_4d_3x3_reduce)
    inception_4d_5x5_reduce = Convolution2D(32,1,1,border_mode='same',activation='relu',name='inception_4d/5x5_reduce',W_regularizer=l2(0.0002))(inception_4c_output)
    inception_4d_5x5 = Convolution2D(64,5,5,border_mode='same',activation='relu',name='inception_4d/5x5',W_regularizer=l2(0.0002))(inception_4d_5x5_reduce)
    inception_4d_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_4d/pool')(inception_4c_output)
    inception_4d_pool_proj = Convolution2D(64,1,1,border_mode='same',activation='relu',name='inception_4d/pool_proj',W_regularizer=l2(0.0002))(inception_4d_pool)
    inception_4d_output = merge([inception_4d_1x1,inception_4d_3x3,inception_4d_5x5,inception_4d_pool_proj],mode='concat',concat_axis=1,name='inception_4d/output')

    loss2_ave_pool = AveragePooling2D(pool_size=(5,5),strides=(3,3),name='loss2/ave_pool')(inception_4d_output)
    loss2_conv = Convolution2D(128,1,1,border_mode='same',activation='relu',name='loss2/conv',W_regularizer=l2(0.0002))(loss2_ave_pool)
    loss2_flat = Flatten()(loss2_conv)
    loss2_fc = Dense(1024,activation='relu',name='loss2/fc',W_regularizer=l2(0.0002))(loss2_flat)
    loss2_drop_fc = Dropout(0.7)(loss2_fc)
    loss2_classifier = Dense(1000,name='loss2/classifier',W_regularizer=l2(0.0002))(loss2_drop_fc)
    loss2_classifier_act = Activation('softmax')(loss2_classifier)

    inception_4e_1x1 = Convolution2D(256,1,1,border_mode='same',activation='relu',name='inception_4e/1x1',W_regularizer=l2(0.0002))(inception_4d_output)
    inception_4e_3x3_reduce = Convolution2D(160,1,1,border_mode='same',activation='relu',name='inception_4e/3x3_reduce',W_regularizer=l2(0.0002))(inception_4d_output)
    inception_4e_3x3 = Convolution2D(320,3,3,border_mode='same',activation='relu',name='inception_4e/3x3',W_regularizer=l2(0.0002))(inception_4e_3x3_reduce)
    inception_4e_5x5_reduce = Convolution2D(32,1,1,border_mode='same',activation='relu',name='inception_4e/5x5_reduce',W_regularizer=l2(0.0002))(inception_4d_output)
    inception_4e_5x5 = Convolution2D(128,5,5,border_mode='same',activation='relu',name='inception_4e/5x5',W_regularizer=l2(0.0002))(inception_4e_5x5_reduce)
    inception_4e_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_4e/pool')(inception_4d_output)
    inception_4e_pool_proj = Convolution2D(128,1,1,border_mode='same',activation='relu',name='inception_4e/pool_proj',W_regularizer=l2(0.0002))(inception_4e_pool)
    inception_4e_output = merge([inception_4e_1x1,inception_4e_3x3,inception_4e_5x5,inception_4e_pool_proj],mode='concat',concat_axis=1,name='inception_4e/output')

    inception_4e_output_zero_pad = ZeroPadding2D(padding=(1, 1))(inception_4e_output)
    pool4_helper = PoolHelper()(inception_4e_output_zero_pad)
    pool4_3x3_s2 = MaxPooling2D(pool_size=(3,3),strides=(2,2),border_mode='valid',name='pool4/3x3_s2')(pool4_helper)

    inception_5a_1x1 = Convolution2D(256,1,1,border_mode='same',activation='relu',name='inception_5a/1x1',W_regularizer=l2(0.0002))(pool4_3x3_s2)
    inception_5a_3x3_reduce = Convolution2D(160,1,1,border_mode='same',activation='relu',name='inception_5a/3x3_reduce',W_regularizer=l2(0.0002))(pool4_3x3_s2)
    inception_5a_3x3 = Convolution2D(320,3,3,border_mode='same',activation='relu',name='inception_5a/3x3',W_regularizer=l2(0.0002))(inception_5a_3x3_reduce)
    inception_5a_5x5_reduce = Convolution2D(32,1,1,border_mode='same',activation='relu',name='inception_5a/5x5_reduce',W_regularizer=l2(0.0002))(pool4_3x3_s2)
    inception_5a_5x5 = Convolution2D(128,5,5,border_mode='same',activation='relu',name='inception_5a/5x5',W_regularizer=l2(0.0002))(inception_5a_5x5_reduce)
    inception_5a_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_5a/pool')(pool4_3x3_s2)
    inception_5a_pool_proj = Convolution2D(128,1,1,border_mode='same',activation='relu',name='inception_5a/pool_proj',W_regularizer=l2(0.0002))(inception_5a_pool)
    inception_5a_output = merge([inception_5a_1x1,inception_5a_3x3,inception_5a_5x5,inception_5a_pool_proj],mode='concat',concat_axis=1,name='inception_5a/output')

    inception_5b_1x1 = Convolution2D(384,1,1,border_mode='same',activation='relu',name='inception_5b/1x1',W_regularizer=l2(0.0002))(inception_5a_output)
    inception_5b_3x3_reduce = Convolution2D(192,1,1,border_mode='same',activation='relu',name='inception_5b/3x3_reduce',W_regularizer=l2(0.0002))(inception_5a_output)
    inception_5b_3x3 = Convolution2D(384,3,3,border_mode='same',activation='relu',name='inception_5b/3x3',W_regularizer=l2(0.0002))(inception_5b_3x3_reduce)
    inception_5b_5x5_reduce = Convolution2D(48,1,1,border_mode='same',activation='relu',name='inception_5b/5x5_reduce',W_regularizer=l2(0.0002))(inception_5a_output)
    inception_5b_5x5 = Convolution2D(128,5,5,border_mode='same',activation='relu',name='inception_5b/5x5',W_regularizer=l2(0.0002))(inception_5b_5x5_reduce)
    inception_5b_pool = MaxPooling2D(pool_size=(3,3),strides=(1,1),border_mode='same',name='inception_5b/pool')(inception_5a_output)
    inception_5b_pool_proj = Convolution2D(128,1,1,border_mode='same',activation='relu',name='inception_5b/pool_proj',W_regularizer=l2(0.0002))(inception_5b_pool)
    inception_5b_output = merge([inception_5b_1x1,inception_5b_3x3,inception_5b_5x5,inception_5b_pool_proj],mode='concat',concat_axis=1,name='inception_5b/output')

    pool5_7x7_s1 = AveragePooling2D(pool_size=(7,7),strides=(1,1),name='pool5/7x7_s2')(inception_5b_output)
    loss3_flat = Flatten()(pool5_7x7_s1)
    pool5_drop_7x7_s1 = Dropout(0.4)(loss3_flat)
    loss3_classifier = Dense(1000,name='loss3/classifier',W_regularizer=l2(0.0002))(pool5_drop_7x7_s1)
    loss3_classifier_act = Activation('softmax',name='prob')(loss3_classifier)

    # Create model
    model = Model(input=input, output=[loss1_classifier_act,loss2_classifier_act,loss3_classifier_act])

    # Load ImageNet pre-trained data
    model.load_weights('imagenet_models/googlenet_weights.h5')

    # Truncate and replace softmax layer for transfer learning
    # Cannot use model.layers.pop() since model is not of Sequential() type
    # The method below works since pre-trained weights are stored in layers but not in the model
    loss1_classifier_statefarm = Dense(num_classes,name='loss1/classifier',W_regularizer=l2(0.0002))(loss1_drop_fc)
    loss1_classifier_act_statefarm = Activation('softmax')(loss1_classifier_statefarm)

    # Create another model with our customized softmax
    model = Model(input=input, output=[loss1_classifier_act_statefarm])
    
    # Learning rate is changed to 0.001
    sgd = SGD(lr=1e-3, decay=1e-6, momentum=0.9, nesterov=True)
    model.compile(optimizer=sgd, loss='categorical_crossentropy', metrics=['accuracy'])

    return model

In [8]:
def vgg19_model(img_rows, img_cols, channel=1, num_classes=None):
    """
    VGG 19 Model for Keras

    Model Schema is based on
    https://gist.github.com/baraldilorenzo/8d096f48a1be4a2d660d

    ImageNet Pretrained Weights
    https://drive.google.com/file/d/0Bz7KyqmuGsilZ2RVeVhKY0FyRmc/view?usp=sharing

    Parameters:
      img_rows, img_cols - resolution of inputs
      channel - 1 for grayscale, 3 for color
      num_classes - number of class labels for our classification task
    """

    model = Sequential()
    model.add(ZeroPadding2D((1,1),input_shape=(channel, img_rows, img_cols)))
    model.add(Convolution2D(64, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(64, 3, 3, activation='relu'))
    model.add(MaxPooling2D((2,2), strides=(2,2)))

    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(128, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(128, 3, 3, activation='relu'))
    model.add(MaxPooling2D((2,2), strides=(2,2)))

    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(256, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(256, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(256, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(256, 3, 3, activation='relu'))
    model.add(MaxPooling2D((2,2), strides=(2,2)))
    
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(MaxPooling2D((2,2), strides=(2,2)))

    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(ZeroPadding2D((1,1)))
    model.add(Convolution2D(512, 3, 3, activation='relu'))
    model.add(MaxPooling2D((2,2), strides=(2,2)))

    # Add Fully Connected Layer
    model.add(Flatten())
    model.add(Dense(4096, activation='relu'))
    model.add(Dropout(0.5))
    model.add(Dense(4096, activation='relu'))
    model.add(Dropout(0.5))
    model.add(Dense(1000, activation='softmax'))

    # Loads ImageNet pre-trained data
    model.load_weights('imagenet_models/vgg19_weights.h5')

    # Truncate and replace softmax layer for transfer learning
    model.layers.pop()
    model.outputs = [model.layers[-1].output]
    model.layers[-1].outbound_nodes = []
    model.add(Dense(num_classes, activation='softmax'))

    # Learning rate is changed to 0.001
    sgd = SGD(lr=1e-3, decay=1e-6, momentum=0.9, nesterov=True)
    model.compile(optimizer=sgd, loss='categorical_crossentropy', metrics=['accuracy', 'top_k_categorical_accuracy'])

    return model

In [3]:
def check_count_correct(filenames, classes):
    assert(len(filenames) == len(classes))
    correct = incorrect = 0
    for i in range(len(filenames)):
        if filenames[i].split('/')[0] == classes[i]:
            correct += 1
        else:
            incorrect += 1
    return correct, incorrect

In [4]:
if __name__ == '__main__':

    # Example to fine-tune on 3000 samples from Cifar10

    img_rows, img_cols = 224, 224 # Resolution of inputs
    channel = 3

    BATCH_SIZE = 64
    DATA_PATH = "../../data/compcars/data/image/"
    batches = jeremy_vgg16.Vgg16().get_batches(DATA_PATH+'train',
                                     gen=image.ImageDataGenerator(preprocessing_function=jeremy_vgg16.vgg_preprocess),
                                     batch_size=BATCH_SIZE)
    val_batches = jeremy_vgg16.Vgg16().get_batches(DATA_PATH+'valid',
                                         gen=image.ImageDataGenerator(preprocessing_function=jeremy_vgg16.vgg_preprocess),
                                         batch_size=BATCH_SIZE)

    model = googlenet_model(img_rows, img_cols, channel, batches.nb_class)
    model.load_weights('inception_model_adam_100.h5')
    test_batches = jeremy_vgg16.Vgg16().get_batches(DATA_PATH+'test', gen=image.ImageDataGenerator(preprocessing_function=jeremy_vgg16.vgg_preprocess), shuffle=False, batch_size=BATCH_SIZE, class_mode=None)
    probs = model.predict_generator(test_batches, test_batches.nb_sample)
    print probs
    labels = test_batches.classes
    filenames = test_batches.filenames
    print labels
    print filenames
    labels_predicted = [np.argmax(prob) for prob in probs]
    classes_ids = list(iter(batches.class_indices)) # get a list of all the class labels
    for c in batches.class_indices:
        classes_ids[batches.class_indices[c]] = c
    classes = [classes_ids[idx] for idx in labels_predicted]
    correct, incorrect = check_count_correct(filenames, classes)
    print correct
    print incorrect


Found 13861 images belonging to 431 classes.
Found 2155 images belonging to 431 classes.
Found 14939 images belonging to 431 classes.
[[  3.42704095e-02   9.00431842e-05   2.50467539e-01 ...,   2.11162933e-05
    1.70056337e-05   1.02738875e-06]
 [  9.92460668e-01   7.43978390e-08   4.13845964e-06 ...,   4.10631037e-05
    2.50655262e-06   2.88339879e-06]
 [  6.35309637e-01   9.41724982e-04   1.61943061e-03 ...,   3.14970612e-06
    2.45621231e-06   4.91439960e-06]
 ..., 
 [  2.62345543e-06   7.52759252e-06   3.58249895e-06 ...,   3.12873954e-06
    2.53909072e-08   1.57111898e-01]
 [  2.09854556e-06   4.13891321e-08   3.43503692e-04 ...,   1.37009061e-04
    1.75171493e-07   1.18110947e-01]
 [  8.52001976e-05   1.25610513e-05   4.39319061e-03 ...,   2.36209831e-04
    8.50007893e-07   8.08204412e-02]]
[  0   0   0 ..., 430 430 430]
['100_211/a920ae289fc479.jpg', '100_211/b294f935712384.jpg', '100_211/718ac24fdeb0b1.jpg', '100_211/f12e1276172293.jpg', '100_211/0c55734d1a96ac.jpg', '100

In [5]:
    top_5_labels_pred = [np.argpartition(prob, -5)[-5:] for prob in probs]
    print top_5_labels_pred
    classes_top_5 = []
    for i in range(len(top_5_labels_pred)):
        classes_temp = [classes_ids[idx] for idx in top_5_labels_pred[i]]
        classes_top_5.append(classes_temp)
    print classes_top_5

[array([332, 328, 137,   2, 421]), array([257, 179,  15, 332,   0]), array([167, 286,   5,  69,   0]), array([ 44, 359, 374, 167, 269]), array([349, 332,  86,  73,   0]), array([276,   0, 286,  86, 256]), array([429, 279, 258, 428,   0]), array([182, 373, 366, 371, 374]), array([ 92,  64, 340, 334, 420]), array([177,  81, 421, 298,   0]), array([256,  15,  42, 421,   0]), array([111, 346, 425, 228, 226]), array([ 53, 272,  31, 164,   0]), array([282, 284,   4,   5, 427]), array([373,   0, 188,   5, 374]), array([332, 334, 204, 256,   0]), array([425,   0, 407,  39, 228]), array([187, 298, 258, 365,   0]), array([352, 256, 311,   2,   0]), array([340,  56, 228, 278, 407]), array([423, 365,  49,   0, 161]), array([278, 427,   0, 298, 253]), array([353, 256, 421,  15, 241]), array([  5,  61, 204, 256,   0]), array([187, 347, 231, 199,   0]), array([226,  87, 259, 407,  61]), array([257,  92, 280, 365,   0]), array([223,  79, 221,  94,   0]), array([ 16, 182,   0,  92,  44]), array([117, 2

In [6]:
def check_count_correct_top_5(filenames, classes_top_5):
    assert(len(filenames) == len(classes_top_5))
    correct = incorrect = 0
    for i in range(len(filenames)):
        if filenames[i].split('/')[0] in classes_top_5[i]:
            correct += 1
        else:
            incorrect += 1
    return correct, incorrect

In [7]:
check_count_correct_top_5(filenames, classes_top_5)

(10917, 4022)

In [12]:
    batches = jeremy_vgg16.Vgg16().get_batches(DATA_PATH+'train',
                                     gen=image.ImageDataGenerator(preprocessing_function=jeremy_vgg16.vgg_preprocess),
                                     batch_size=BATCH_SIZE)
    val_batches = jeremy_vgg16.Vgg16().get_batches(DATA_PATH+'valid',
                                         gen=image.ImageDataGenerator(preprocessing_function=jeremy_vgg16.vgg_preprocess),
                                         batch_size=BATCH_SIZE)
    test_batches = jeremy_vgg16.Vgg16().get_batches(DATA_PATH+'test', gen=image.ImageDataGenerator(preprocessing_function=jeremy_vgg16.vgg_preprocess), shuffle=False, batch_size=BATCH_SIZE, class_mode=None)
    model_vgg19 = vgg19_model(img_rows, img_cols, channel, batches.nb_class)
    model_vgg19.load_weights('vgg19_model_60.h5')
    probs_vgg19 = model_vgg19.predict_generator(test_batches, test_batches.nb_sample)
    print probs_vgg19
    labels_vgg19 = test_batches.classes
    print labels_vgg19
    labels_predicted_vgg19 = [np.argmax(prob) for prob in probs_vgg19]
    classes_vgg19 = [classes_ids[idx] for idx in labels_predicted_vgg19]
    correct_vgg19, incorrect_vgg19 = check_count_correct(filenames, classes_vgg19)
    print correct_vgg19
    print incorrect_vgg19

Found 13861 images belonging to 431 classes.
Found 2155 images belonging to 431 classes.
Found 14939 images belonging to 431 classes.
[[  1.00000000e+00   3.71153420e-11   3.22141730e-10 ...,   9.53799587e-15
    4.73342636e-15   6.40279913e-15]
 [  1.00000000e+00   2.33972232e-16   3.73778004e-17 ...,   2.03657838e-19
    1.08693828e-18   5.55037028e-20]
 [  9.89580333e-01   5.32661090e-07   1.85844851e-08 ...,   3.25862198e-10
    1.92691724e-10   1.96344635e-10]
 ..., 
 [  5.58806864e-12   1.34767273e-12   6.70251877e-17 ...,   1.53601036e-13
    8.54021731e-15   9.99999642e-01]
 [  7.85421950e-09   5.01346742e-09   8.21958446e-10 ...,   1.65328970e-07
    2.20785559e-08   9.95325804e-01]
 [  8.09697394e-06   3.08627750e-05   2.27795249e-06 ...,   5.52675317e-07
    2.31938472e-07   9.12480354e-02]]
[  0   0   0 ..., 430 430 430]
9249
5690


In [13]:
    top_5_labels_pred_vgg19 = [np.argpartition(prob, -5)[-5:] for prob in probs_vgg19] # get indices for top 5 probs
    print top_5_labels_pred_vgg19
    classes_top_5_vgg19 = []
    for i in range(len(top_5_labels_pred_vgg19)):
        classes_temp = [classes_ids[idx] for idx in top_5_labels_pred_vgg19[i]]
        classes_top_5_vgg19.append(classes_temp)
    print classes_top_5_vgg19

[array([311,   6, 278,  50,   0]), array([ 18,   6, 278,  50,   0]), array([117, 334,  15,   5,   0]), array([366,  77, 388, 374,   5]), array([133,  41, 334,   5,   0]), array([278, 340,  41,  44,   0]), array([278,  61,   6,  18,   0]), array([  0,  77,   5, 188, 373]), array([110, 334,  97, 340, 196]), array([275, 298, 187, 340,   0]), array([ 90, 117, 272, 352,   0]), array([ 18, 340, 413,   6, 111]), array([135, 352, 272,  33,   0]), array([ 38,   0, 425,  39,  75]), array([ 77,   5, 362, 278,   0]), array([308, 422,   6,  17,   0]), array([351,   2,  97, 340,  70]), array([421, 350, 422,   6,   0]), array([301, 421,  64,  31,   0]), array([  0, 274, 275,  99, 278]), array([  6, 304,  18, 340,   0]), array([117,  44,   5, 410,   0]), array([ 81, 352,  86, 272,   0]), array([422,   5,   6, 407,   0]), array([246,  27, 340, 275,   0]), array([ 61, 187,   2,   0, 113]), array([  2,   6,  15, 421,   0]), array([298,  27, 340, 187,   0]), array([  1, 117,  64, 113,   0]), array([422, 2

In [15]:
check_count_correct_top_5(filenames, classes_top_5_vgg19)

(12092, 2847)

In [24]:
def check_count_correct_top_5_in_both(filenames, classes_top_5_a, classes_top_5_b):
    assert(len(filenames) == len(classes_top_5_a) and len(filenames) == len(classes_top_5_b))
    correct = incorrect = 0
    for i in range(len(filenames)):
        if filenames[i].split('/')[0] in classes_top_5_a[i] or filenames[i].split('/')[0] in classes_top_5_b[i]:
            correct += 1
        else:
            incorrect += 1
    return correct, incorrect

In [25]:
check_count_correct_top_5_in_both(filenames, classes_top_5, classes_top_5_vgg19) # no significance of this metric

(13030, 1909)

In [39]:
def average_both_probs(probs_a, probs_b):
    assert(len(probs_a) == len(probs_b))
    final = []
    for i in range(len(probs_a)):
        temp = []
        for j in range(len(probs_a[i])):
            temp.append((probs_a[i][j]+probs_b[i][j])/2)
        final.append(temp)
    return final

In [41]:
avg_probs = average_both_probs(probs, probs_vgg19)

In [42]:
    labels_combined = test_batches.classes
    print labels_combined
    labels_predicted_combined = [np.argmax(prob) for prob in avg_probs]
    classes_combined = [classes_ids[idx] for idx in labels_predicted_combined]
    correct_combined, incorrect_combined = check_count_correct(filenames, classes_combined)
    print correct_combined
    print incorrect_combined

[  0   0   0 ..., 430 430 430]
9634
5305


In [43]:
    top_5_labels_pred_combined = [np.argpartition(prob, -5)[-5:] for prob in avg_probs] # get indices for top 5 probs
    print top_5_labels_pred_combined
    classes_top_5_combined = []
    for i in range(len(top_5_labels_pred_combined)):
        classes_temp = [classes_ids[idx] for idx in top_5_labels_pred_combined[i]]
        classes_top_5_combined.append(classes_temp)
    print classes_top_5_combined

[array([328, 137, 421,   2,   0]), array([257, 179,  15, 332,   0]), array([167,  69, 286,   5,   0]), array([269, 374,   5, 388, 167]), array([332,  86,   5,  73,   0]), array([ 44, 256,  86, 286,   0]), array([429, 279, 258, 428,   0]), array([373, 374,   5,  77, 371]), array([420,  97, 196, 340, 334]), array([177,  81, 421, 298,   0]), array([256,  15,  42, 421,   0]), array([346, 425, 226, 228, 111]), array([ 53, 272,  31, 164,   0]), array([  4, 427,  39,   5, 425]), array([373, 374, 188,   5,   0]), array([332, 334, 204, 256,   0]), array([340,  70,  39, 407, 228]), array([421, 350, 422,   6,   0]), array([352, 256,   2, 311,   0]), array([ 56, 407, 228,  99, 278]), array([423, 365, 161,  49,   0]), array([278, 427, 298, 253,   0]), array([256, 241, 421,  15,   0]), array([  5, 256, 204, 407,   0]), array([275, 347, 231, 199,   0]), array([259,   0, 407,  61, 113]), array([257, 280,  92, 365,   0]), array([298, 187,  27, 340,   0]), array([182, 113,  44,  92,   0]), array([421,  

In [44]:
check_count_correct_top_5(filenames, classes_top_5_combined)

(12280, 2659)